# Routing Assignment

Congratulations! You just convinced a group of investors to put money into your startup competing against _Instacart_ for delivering specialty pet supplies for hamster grooming. Immediately upon publishing your website, the City of Dallas signs up to have a pallet of hamster grooming supplies delivered to "1500 Marilla Street, Dallas, TX" (Dallas City Hall--where all office animals are banned except hamsters). In addition, you received an order from Annamelissa Uhumehlemehe (a well-known childish hamster lady) who lives at "11322 Cactus Lane, Dallas, TX". You notice other addresses rolling in--_all in the City of Dallas_ (none in Garland, Grand Prarie, Ft. Worth, etc.). So you better hurry because you don't want to lose out on sales!

You immediately go to the https://openstreetmap.org website and verify that these addresses are good addresses in OpenStreetMap including your warehouse at "5351 Fults Blvd., Dallas, TX" (just off Samuell Blvd., and South Buckner). One of your investors' requirements is that you not spend money on Google products or any other product. _You must use OpenStreetMap_ for your routing application.

Your project is to write an application that optimizes deliveries to 20 addresses at a time in the City of Dallas using OpenStreetMap's API. You may pick 18 other addresses at random but, be careful to validate them in OpenStreetMap. Here are some address details:

- Starting (warehouse) address is "5351 Fults Blvd., Dallas, TX"
- You must include "1500 Marilla Street, Dallas, TX", and "11322 Cactus Lane, Dallas, TX" in your list of delivery addresses
- You may pick 18 other addresses but they also have to process any verified list of OpenStreetMap-valid addresses

Your application must:

- Optimize the route starting from your warehouse address with the shortest distance to complete the route
- Display the destinations and the distance between them (refer to the example in the assignment on Canvas)
- Display a map with the most efficient route displayed (refer to the example in the assignment on Canvas)
- Accept a list of up to 20 delivery addresses in Dallas and generate a new route list and map
- Oh wait! The example on Canvas shows distances in km! We use **miles** here so don't forget to convert!

The rubric for this assignment includes:

- All required components are present and your program works as per the specifications (above)
- Additional innovations may be (should be) added to differentiate your app from your classmates
- Your program is well-commented and demonstrates that you know how it works
- Any and all functions should include _docstrings_ that appear when the "help( )" function is called
- The class presentation is excellent

The cells below instantiate packages that may be of use as a starting place. You may alter them but remember: _you must use OpenStreetMap_ to complete this assignment.

In [1]:
import osmnx as ox
import networkx as nx
from geopy.geocoders import Nominatim
import folium
from itertools import permutations
import pandas as pd
from typing import List, Tuple, Dict
import time

In [2]:
class DeliveryRouter:
    """
    A class to optimize delivery routes for hamster supply deliveries in Dallas
    using OpenStreetMap data.
    """
    
    def __init__(self):
        """Initialize the router with Dallas map data"""
        self.geolocator = Nominatim(user_agent="hamster_delivery_router")
        print("Loading Dallas street network...")
        self.dallas_graph = ox.graph_from_place('Dallas, Texas, USA', network_type='drive')
        self.dallas_graph_proj = ox.project_graph(self.dallas_graph)
        
    def validate_address(self, address: str) -> Tuple[bool, tuple]:
        """Validate a Dallas address and return its coordinates"""
        try:
            location = self.geolocator.geocode(address, timeout=10)
            if location and "Dallas" in location.address:
                return True, (location.latitude, location.longitude)
            return False, None
        except Exception as e:
            print(f"Error validating address {address}: {str(e)}")
            return False, None
            
    def calculate_route(self, start_coords: Tuple[float, float], 
                       end_coords: Tuple[float, float]) -> Tuple[float, List[Tuple[float, float]]]:
        """Calculate the shortest route between two points and return distance and path"""
        start_node = ox.nearest_nodes(self.dallas_graph, start_coords[1], start_coords[0])
        end_node = ox.nearest_nodes(self.dallas_graph, end_coords[1], end_coords[0])
        
        try:
            route = nx.shortest_path(self.dallas_graph_proj, start_node, end_node, weight='length')
            distance = sum(ox.utils_graph.get_route_edge_attributes(self.dallas_graph_proj, route, 'length'))
            
            # Get the actual path coordinates for mapping
            path_coords = []
            for node in route:
                y = self.dallas_graph.nodes[node]['y']
                x = self.dallas_graph.nodes[node]['x']
                path_coords.append((y, x))
                
            return distance, path_coords
        except nx.NetworkXNoPath:
            return float('inf'), []

    def optimize_route(self, addresses: List[str]) -> Tuple[List[str], List[float], List[List[Tuple[float, float]]]]:
        """Find the optimal delivery route"""
        # Validate addresses and get coordinates
        locations = []
        for addr in addresses:
            valid, coords = self.validate_address(addr)
            if valid:
                locations.append((addr, coords))
            else:
                raise ValueError(f"Invalid address: {addr}")

        # Warehouse is always first
        warehouse = locations[0]
        delivery_points = locations[1:]
        
        # Find best route
        best_distance = float('inf')
        best_route = None
        best_paths = None
        
        for perm in permutations(delivery_points):
            current_distance = 0
            current_paths = []
            valid_route = True
            route = [warehouse] + list(perm) + [warehouse]
            
            for i in range(len(route) - 1):
                distance, path = self.calculate_route(route[i][1], route[i + 1][1])
                if distance == float('inf'):
                    valid_route = False
                    break
                current_distance += distance
                current_paths.append(path)
                
            if valid_route and current_distance < best_distance:
                best_distance = current_distance
                best_route = route
                best_paths = current_paths
                
        return [loc[0] for loc in best_route], best_distance, best_paths

    def create_visualization(self, addresses: List[str], total_distance: float, 
                           paths: List[List[Tuple[float, float]]]) -> None:
        """Create and save route visualization"""
        # Create base map centered on Dallas
        dallas_center = [32.7767, -96.7970]
        m = folium.Map(location=dallas_center, zoom_start=12)
        
        # Add markers
        # a loop iterates through the addresses list, and each address is validated using self.validate_address, which checks the address formats and brings back coordinates
        # markers are added to the map using folium.marker, the first marker is colored red to distinguish it as the starting point, and subsequent markers are colored blue to denote regular stops
        # a popup on each marker displays the stop number and address
        # this section visually represents all stops on the map, making it easy to identify locations and their sequence
        for i, addr in enumerate(addresses[:-1]):  # Skip last duplicate warehouse
            coords = self.validate_address(addr)[1]
            color = 'red' if i == 0 else 'blue'
            folium.Marker(
                coords,
                popup=f"Stop {i}: {addr}",
                icon=folium.Icon(color=color)
            ).add_to(m)
        
        # Add route paths
        # For each path,  blue polyline is drawn on the map using folium.Polyline, wweight sets  the line thickness and opacity makes the line transparent for better readability
        # this section shows the optimized path
        for path in paths:
            folium.PolyLine(
                path,
                weight=2,
                color='blue',
                opacity=0.8
            ).add_to(m)
        
        # Save map
        # the folium mp object m is saved as an HTML file named optimized_route.html
        m.save('optimized_route.html')
        
        # Print route details
        # A loop iterates through consecutive pairs of addresses in the optimized list
        # For each pai the shortest path is calculated using NetworkX, and geographic data from OSMnx
        # The total segment distance is calculated by summing the length of the edges in the path, and distances are converted from miles to kms and dispayed
        print("\nOptimized Route with Distances:")
        for i in range(len(addresses) - 1):
            distance_km = sum(ox.utils_graph.get_route_edge_attributes(
                self.dallas_graph_proj, 
                nx.shortest_path(self.dallas_graph_proj,
                    ox.nearest_nodes(self.dallas_graph,
                        self.validate_address(addresses[i])[1][1],
                        self.validate_address(addresses[i])[1][0]),
                    ox.nearest_nodes(self.dallas_graph,
                        self.validate_address(addresses[i+1])[1][1],
                        self.validate_address(addresses[i+1])[1][0])),
                'length')) / 1000
            distance_mi = distance_km * 0.621371
            print(f"{addresses[i]} -> {addresses[i+1]}: {distance_km:.2f} km ({distance_mi:.2f} mi)")
            
        # The total distance for the optimized route is printed in both ks and miles
        print(f"Total distance: {total_distance/1000:.2f} km ({total_distance*0.000621371:.2f} mi)")
        
    def display_route_info(self, addresses: List[str], total_distance: float):
        """Display route information directly in the notebook"""
        print("\n=== OPTIMIZED DELIVERY ROUTE ===")
        print("\nRoute Sequence:")
        for i, addr in enumerate(addresses[:-1]):  # Skip last duplicate warehouse
            print(f"Stop {i:2d}: {addr}")
        
        print("\nSegment Distances:")
        for i in range(len(addresses) - 1):
            start_addr = addresses[i]
            end_addr = addresses[i + 1]
            
            # Calculate segment distance
            start_coords = self.validate_address(start_addr)[1]
            end_coords = self.validate_address(end_addr)[1]
            distance, _ = self.calculate_route(start_coords, end_coords)
            
            # Convert to km and miles
            distance_km = distance / 1000
            distance_mi = distance_km * 0.621371
            
            print(f"Segment {i:2d}: {distance_km:6.2f} km ({distance_mi:6.2f} mi)")
            print(f"         {start_addr} -> {end_addr}")

        # Print total distance
        total_km = total_distance / 1000
        total_mi = total_km * 0.621371
        print("\nTotal Route Distance:")
        print(f"  {total_km:.2f} kilometers")
        print(f"  {total_mi:.2f} miles")

In [3]:
# Create router instance
router = DeliveryRouter()

addresses = [ "5351 Fults Blvd., Dallas, TX", "4078 Creekdale Drive, Dallas, TX", "7526 Morton Street, Dallas, TX", "2418 Montalba Avenue, Dallas, TX", "1412 Moran Drive, Dallas, TX", "6211 Annapolis Lane, Dallas, TX", "8814 Redondo Drive, Dallas, TX", "2925 Lenway Street, Dallas, TX", "3203 Bertrand Avenue, Dallas, TX", "7042 Desco Drive, Dallas, TX", "8332 Moorcroft Drive, Dallas, TX", "3724 Purdue Street, Dallas, TX", "7616 Dandy Lane, Dallas, TX", "1249 Olden Street, Dallas, TX", "1014 Delaware Avenue, Dallas, TX", "7318 Crownrich Lane, Dallas, TX", "1634 Engle Avenue, Dallas, TX", "6218 Velasco Avenue, Dallas, TX", "1500 Marilla Street, Dallas, TX", "534 Elkhart Avenue, Dallas, TX", "11322 Cactus Lane, Dallas, TX", "8855 Liptonshire, Dallas, TX", "10223 Clary Drive, Dallas, TX", "9731 Champa Drive, Dallas, TX", "11635 Sahara Way, Dallas, TX", "12167 Ridgelake Drive, Dallas, TX", "11008 Ridgemeadow Drive, Dallas, TX", "10357 Bel Aire, Dallas, TX" ]



# Calculate optimal route
try:
    optimized_addresses, total_distance, paths = router.optimize_route(addresses)
    # router.create_visualization(optimized_addresses, total_distance, paths)
    router.display_route_info(optimized_addresses, total_distance)
    print("\nRoute optimization complete! Check 'optimized_route.html' for the map visualization.")
except Exception as e:
    print(f"Error: {str(e)}")

Loading Dallas street network...


/var/folders/sd/j5p08m515kd7n9549lkkz_q40000gn/T/ipykernel_36090/2698843370.py:33: FutureWarning: The `get_route_edge_attributes` function has been deprecated and will be removed in the v2.0.0 release. Use the `routing.route_to_gdf` function instead. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  distance = sum(ox.utils_graph.get_route_edge_attributes(self.dallas_graph_proj, route, 'length'))
/var/folders/sd/j5p08m515kd7n9549lkkz_q40000gn/T/ipykernel_36090/2698843370.py:33: FutureWarning: The `get_route_edge_attributes` function has been deprecated and will be removed in the v2.0.0 release. Use the `routing.route_to_gdf` function instead. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  distance = sum(ox.utils_graph.get_route_edge_attributes(self.dallas_graph_proj, route, 'length'))
/var/folders/sd/j5p08m515kd7n9549lkkz_q40000gn/T/ipykernel_36090/2698843370.py:33: FutureWarning: The `get_route_edge_attributes` function h